# Segmenting and Clustering Neighborhoods in New York City & London

In [1]:
#install packages
!pip install numpy
!pip install pandas
!pip install requests
!pip install bs4
!pip install plotly
!conda install -c conda-forge geopy --yes
!conda install -c conda-forge folium=0.5.0 --yes
!pip install html5lib
!pip install OSGridConverter
print('Packages installed.')

     |████████████████████████████████| 115 kB 4.5 MB/s eta 0:00:01
  Created wheel for bs4: filename=bs4-0.0.1-py3-none-any.whl size=1273 sha256=0b9d0f3ba25a445bb30b92e1b1870baa21a1d2c1cf62eed2d6ea77c57aea1f3e
  Stored in directory: /home/jovyan/.cache/pip/wheels/19/f5/6d/a97dd4f22376d4472d5f4c76c7646876052ff3166b3cf71050
Successfully built bs4
     |████████████████████████████████| 19.1 MB 4.4 MB/s eta 0:00:01
Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.9.2
  latest version: 4.10.1

Please update conda by running

    $ conda update -n base conda



## Package Plan ##

  environment location: /srv/conda/envs/notebook

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2021.5.30  |       ha878542_0         136 KB  conda-forge
    certifi-2021.5.30          |   py36h5fab9bb_0      

In [2]:
#import libraries
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json
import requests
from pandas.io.json import json_normalize
from bs4 import BeautifulSoup
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from geopy.geocoders import Nominatim
from OSGridConverter import grid2latlong
import folium
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
print('Libraries imported.')

Libraries imported.


## Set Up Foursquare Credentials and Venue Functions

In [3]:
#input Foursquare credentials
CLIENT_ID = 'YTE1O5DN3TRLBFJR2V4CMOU0SNG2AF3XQA0CGFA4KA4SFAOK' # your Foursquare ID
CLIENT_SECRET = 'SRMIKFL2VBEBVO3ADRTIEDTRAB5OPAS4HOPTF00PXTOVXWT3' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

In [4]:
#function to get the top 100 venues that for given neighborhood within a radius of 750 meters

def getNearbyVenues(names, latitudes, longitudes, radius= 750):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood',
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [5]:
#function to sort the venues in descending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

## NYC : Download Data from IBM Server and Transform into Pandas Dataframe 

In [6]:
#download NYC dataset from IBM server
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json

In [7]:
#load data 
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [8]:
#get a feel for how the data is structured
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [9]:
#all the relevant data is located within "features"
nyc_neighborhoods_data = newyork_data['features']

In [10]:
# define the dataframe columns
column_names = ['City','Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe (creating an empty dataframe)
nyc_neighborhoods = pd.DataFrame(columns=column_names)

In [11]:
#transform data into pandas dataframe
for data in nyc_neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    city = 'New York City'
    
    nyc_neighborhoods = nyc_neighborhoods.append({'City': city, 'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [12]:
#populated dataframe with nyc data 
nyc_neighborhoods.head()

City Borough Neighborhood   Latitude  Longitude
0  New York City   Bronx    Wakefield  40.894705 -73.847201
1  New York City   Bronx   Co-op City  40.874294 -73.829939
2  New York City   Bronx  Eastchester  40.887556 -73.827806
3  New York City   Bronx    Fieldston  40.895437 -73.905643
4  New York City   Bronx    Riverdale  40.890834 -73.912585

In [13]:
#merge neighborhood and borough into one column
nyc_neighborhoods['Neighborhood'] = nyc_neighborhoods['Neighborhood'] + " (" + nyc_neighborhoods['Borough'] + ")"
nyc_neighborhoods.drop(columns = 'Borough', inplace=True)
nyc_neighborhoods.head()

City         Neighborhood   Latitude  Longitude
0  New York City    Wakefield (Bronx)  40.894705 -73.847201
1  New York City   Co-op City (Bronx)  40.874294 -73.829939
2  New York City  Eastchester (Bronx)  40.887556 -73.827806
3  New York City    Fieldston (Bronx)  40.895437 -73.905643
4  New York City    Riverdale (Bronx)  40.890834 -73.912585

In [14]:
#verify the number of rows and columns
nyc_neighborhoods.shape

(306, 4)

## London: Webscrape Data from Wiki Page and Transform into Pandas Dataframe

In [15]:
#download webpage and save text in the html_data variable
london_url = "https://en.wikipedia.org/wiki/List_of_areas_of_London" 
html_data = requests.get(london_url).text

In [16]:
#parse through the html data
soup = BeautifulSoup(html_data,"html.parser")

In [17]:
#find all tables
tables = soup.find_all('table')

In [18]:
#create empty list to store cleansed data
table_contents=[]

#extract the html data and assign it to the corresponding column
row_num = 0
for row in tables[1].find("tbody").find_all("tr"):
    if row_num > 0: #want to skip the first row as that contains a heading (refine later so that there's no need to skip row) 
        cell = {} #create a dictionary to hold all record values
        col = row.find_all('td')
        remove_tail_borough = col[1].text.split('[')
        cell['Borough']= remove_tail_borough[0]
        cell['Neighborhood'] = col[0].text
        cell['PostTown'] = col[2].text
        cell['OSGridRef'] = col[5].text.replace('\n','')
        if cell['OSGridRef'] == '': #use the OS grid to find the coordinates
            cell['Latitude'] = 0
            cell['Longitude'] = 0 
        else:
            l=grid2latlong(cell['OSGridRef']) 
            cell['Latitude'] = l.latitude 
            cell['Longitude'] = l.longitude
        table_contents.append(cell) #consolidate all dictionaries into a list 
    row_num = row_num + 1
df=pd.DataFrame(table_contents) #convert list into dataframe

#print dataframe
df.head()

Borough Neighborhood        PostTown OSGridRef  \
0             Bexley,  Greenwich    Abbey Wood          LONDON  TQ465785   
1  Ealing, Hammersmith and Fulham        Acton          LONDON  TQ205805   
2                         Croydon    Addington         CROYDON  TQ375645   
3                         Croydon   Addiscombe         CROYDON  TQ345665   
4                          Bexley  Albany Park  BEXLEY, SIDCUP  TQ478728   

    Latitude  Longitude  
0  51.486484   0.109318  
1  51.510591  -0.264585  
2  51.362934  -0.025780  
3  51.381625  -0.068126  
4  51.434929   0.125663

In [19]:
#verify the number of rows and columns
df.shape

(531, 6)

In [20]:
#filter results for PostTown with London only (records with multiple PostTowns will NOT be included)
london_neighborhoods = df[df['PostTown'] == 'LONDON'].reset_index(drop=True)
london_neighborhoods.head()

Borough Neighborhood PostTown OSGridRef   Latitude  \
0             Bexley,  Greenwich    Abbey Wood   LONDON  TQ465785  51.486484   
1  Ealing, Hammersmith and Fulham        Acton   LONDON  TQ205805  51.510591   
2                            City      Aldgate   LONDON  TQ334813  51.514885   
3                     Westminster      Aldwych   LONDON  TQ307810  51.512819   
4                         Bromley      Anerley   LONDON  TQ345695  51.408585   

   Longitude  
0   0.109318  
1  -0.264585  
2  -0.078356  
3  -0.117388  
4  -0.066989

In [21]:
#verify the number of rows and columns
london_neighborhoods.shape

(297, 6)

In [22]:
#format the London dataframe to match the NYC dataframe so that we can merge them

london_neighborhoods.drop(['PostTown'], axis=1, inplace = True)#drop PostTown column since all of them are London
london_neighborhoods.drop(['OSGridRef'], axis=1, inplace = True)#drop OSGridRef since we already extracted the latitude and longitude
london_neighborhoods['City'] = 'London' #add city column to help distinguish between NYC and London
cols = london_neighborhoods.columns.tolist() #current order of columns 
cols = cols[-1:] + cols[:-1] #move City column to the front
london_neighborhoods[cols].head()

City                         Borough Neighborhood   Latitude  Longitude
0  London             Bexley,  Greenwich    Abbey Wood  51.486484   0.109318
1  London  Ealing, Hammersmith and Fulham        Acton  51.510591  -0.264585
2  London                            City      Aldgate  51.514885  -0.078356
3  London                     Westminster      Aldwych  51.512819  -0.117388
4  London                         Bromley      Anerley  51.408585  -0.066989

In [23]:
#merge neighborhood and borough into one column
london_neighborhoods['Neighborhood'] = london_neighborhoods['Neighborhood'] + " (" + london_neighborhoods['Borough'] + ")"
london_neighborhoods.drop(columns = 'Borough', inplace=True)
london_neighborhoods.head()

Neighborhood   Latitude  Longitude    City
0        Abbey Wood (Bexley,  Greenwich )  51.486484   0.109318  London
1  Acton (Ealing, Hammersmith and Fulham)  51.510591  -0.264585  London
2                          Aldgate (City)  51.514885  -0.078356  London
3                   Aldwych (Westminster)  51.512819  -0.117388  London
4                       Anerley (Bromley)  51.408585  -0.066989  London

In [24]:
#verify the number of rows and columns
london_neighborhoods.shape

(297, 4)

In [25]:
#merge the NYC dataframe and London dataframe 
nyc_london_neighborhoods = pd.concat([nyc_neighborhoods, london_neighborhoods]).reset_index(drop=True) 
nyc_london_neighborhoods.tail()

City                              Neighborhood   Latitude  Longitude
598  London                     Wood Green (Haringey)  51.598237  -0.116745
599  London                      Woodford (Redbridge)  51.604820   0.028068
600  London                    Woodside Park (Barnet)  51.617324  -0.186791
601  London                      Woolwich (Greenwich)  51.496238   0.066504
602  London  Wormwood Scrubs (Hammersmith and Fulham)  51.519148  -0.235411

In [26]:
#verify the number of rows and columns
nyc_london_neighborhoods.shape

(603, 4)

## Use Folium Map to Visualize Neighborhoods in NYC and London

In [27]:
#obtain geographic coordinates of NYC
nyc_address = 'New York City, NY'

nyc_geolocator = Nominatim(user_agent="ny_explorer")
nyc_location = nyc_geolocator.geocode(nyc_address)
nyc_latitude = nyc_location.latitude
nyc_longitude = nyc_location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(nyc_latitude, nyc_longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [28]:
# create map of NYC
map_nyc = folium.Map(location=[nyc_latitude, nyc_longitude], zoom_start=10)

# add markers to map
for lat, lng, neighborhood in zip(nyc_london_neighborhoods['Latitude'], nyc_london_neighborhoods['Longitude'], nyc_london_neighborhoods['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc', fill_opacity=0.7, 
        parse_html=False).add_to(map_nyc)
                                           
map_nyc

In [29]:
#obtain geographic coordinates of London
london_address = 'London, United Kingdom'

london_geolocator = Nominatim(user_agent="uk_explorer")
london_location = london_geolocator.geocode(london_address)
london_latitude = london_location.latitude
london_longitude = london_location.longitude
print('The geograpical coordinate of London are {}, {}.'.format(london_latitude, london_longitude))

The geograpical coordinate of London are 51.5073219, -0.1276474.


In [30]:
# create map of London
map_london = folium.Map(location=[london_latitude, london_longitude], zoom_start=10)

# add markers to map
for lat, lng, neighborhood in zip(nyc_london_neighborhoods['Latitude'], nyc_london_neighborhoods['Longitude'], nyc_london_neighborhoods['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc', fill_opacity=0.7, 
        parse_html=False).add_to(map_london)
                                           
map_london

## Use Foursquare to Identify Top Venues in Each Neighborhood

In [31]:
#run the above function on each neighborhood
nyc_london_venues = getNearbyVenues(names=nyc_london_neighborhoods['Neighborhood'],
                                   latitudes=nyc_london_neighborhoods['Latitude'],
                                   longitudes=nyc_london_neighborhoods['Longitude']
                                  )

Wakefield (Bronx)
Co-op City (Bronx)
Eastchester (Bronx)
Fieldston (Bronx)
Riverdale (Bronx)
Kingsbridge (Bronx)
Marble Hill (Manhattan)
Woodlawn (Bronx)
Norwood (Bronx)
Williamsbridge (Bronx)
Baychester (Bronx)
Pelham Parkway (Bronx)
City Island (Bronx)
Bedford Park (Bronx)
University Heights (Bronx)
Morris Heights (Bronx)
Fordham (Bronx)
East Tremont (Bronx)
West Farms (Bronx)
High  Bridge (Bronx)
Melrose (Bronx)
Mott Haven (Bronx)
Port Morris (Bronx)
Longwood (Bronx)
Hunts Point (Bronx)
Morrisania (Bronx)
Soundview (Bronx)
Clason Point (Bronx)
Throgs Neck (Bronx)
Country Club (Bronx)
Parkchester (Bronx)
Westchester Square (Bronx)
Van Nest (Bronx)
Morris Park (Bronx)
Belmont (Bronx)
Spuyten Duyvil (Bronx)
North Riverdale (Bronx)
Pelham Bay (Bronx)
Schuylerville (Bronx)
Edgewater Park (Bronx)
Castle Hill (Bronx)
Olinville (Bronx)
Pelham Gardens (Bronx)
Concourse (Bronx)
Unionport (Bronx)
Edenwald (Bronx)
Bay Ridge (Brooklyn)
Bensonhurst (Brooklyn)
Sunset Park (Brooklyn)
Greenpoint (Br

In [32]:
#verify the number of rows and columns
nyc_london_venues.shape

(29451, 7)

In [33]:
#group the venues by neighborhood
nyc_london_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Abbey Wood (Bexley,  Greenwich )                                        4   
Acton (Ealing, Hammersmith and Fulham)                                 26   
Aldgate (City)                                                        100   
Aldwych (Westminster)                                                 100   
Allerton (Bronx)                                                       40   
Anerley (Bromley)                                                      12   
Angel (Islington)                                                      15   
Annadale (Staten Island)                                               12   
Archway (Islington)                                                    36   
Arden Heights (Staten Island)                                          13   
Arlington (Staten Island)                                               9   
Arnos Grove (Enfield)                                                   8   
Arrochar (Staten Island)                                               27   
Arverne (Queens)                                                       27   
Astoria (Queens)                                                      100   
Astoria Heights (Queens)                                               34   
Auburndale (Queens)                                                    66   
Balham (Wandsworth)                                                    62   
Bankside (Southwark)                                                  100   
Barbican (City)                                                       100   
Barnes (Richmond upon Thames)                                          24   
Barnsbury (Islington)                                                  42   
Bath Beach (Brooklyn)                                                  81   
Battersea (Wandsworth)                                                 36   
Battery Park City (Manhattan)                                         100   
Bay Ridge (Brooklyn)                                                  100   
Bay Terrace (Queens)                                                   39   
Bay Terrace (Staten Island)                                            17   
Baychester (Bronx)                                                     64   
Bayside (Queens)                                                       80   
Bayswater (Queens)                                                      5   
Bayswater (Westminster)                                               100   
Bedford Park (Bronx)                                                   57   
Bedford Park (Ealing)                                                  19   
Bedford Stuyvesant (Brooklyn)                                          68   
Beechhurst (Queens)                                                    33   
Belgravia (Westminster)                                               100   
Bellaire (Queens)                                                      31   
Belle Harbor (Queens)                                                  24   
Bellerose (Queens)                                                     37   
Bellingham (Lewisham)                                                  10   
Belmont (Bronx)                                                        87   
Belsize Park (Camden)                                                  93   
Bensonhurst (Brooklyn)                                                 44   
Bergen Beach (Brooklyn)                                                 9   
Bermondsey (Southwark)                                                100   
Bethnal Green (Tower Hamlets)                                         100   
Blackfriars (City)                                                    100   
Blackheath (Lewisham)                                                  37   
Blackheath Royal Standard (Greenwich)                                  23   
Blackwall (Tower Hamlets)                       

In [34]:
#unique categories for venues
print('There are {} uniques categories.'.format(len(nyc_london_venues['Venue Category'].unique())))

There are 524 uniques categories.


In [35]:
#Analyze Each Neighborhood

# one hot encoding
nyc_london_onehot = pd.get_dummies(nyc_london_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
nyc_london_onehot['Neighborhood']= nyc_london_venues['Neighborhood']
neighborhood_col_index = nyc_london_onehot.columns.get_loc("Neighborhood")

#move neighborhood column to the first column 
fixed_columns = [nyc_london_onehot.columns[neighborhood_col_index]] + list(nyc_london_onehot.columns[0:neighborhood_col_index]) + list(nyc_london_onehot.columns[neighborhood_col_index + 1:])
nyc_london_onehot = nyc_london_onehot[fixed_columns]


print("The unique venue categories have now become columns.") 
print("Therefore the column count should equal the number of unique categories:", len(nyc_london_onehot.columns))


nyc_london_onehot.head()

The unique venue categories have now become columns.
Therefore the column count should equal the number of unique categories: 524


Neighborhood  ATM  Accessories Store  Adult Boutique  \
0  Wakefield (Bronx)    0                  0               0   
1  Wakefield (Bronx)    0                  0               0   
2  Wakefield (Bronx)    0                  0               0   
3  Wakefield (Bronx)    0                  0               0   
4  Wakefield (Bronx)    0                  0               0   

   Afghan Restaurant  African Restaurant  Airport Lounge  American Restaurant  \
0                  0                   0               0                    0   
1                  0                   0               0                    0   
2                  0                   0               0                    0   
3                  0                   0               0                    0   
4                  0                   0               0                    0   

   Animal Shelter  Antique Shop  Aquarium  Arcade  Arepa Restaurant  \
0               0             0         0       0                 0   
1               0             0         0       0                 0   
2               0             0         0       0                 0   
3               0             0         0       0                 0   
4               0             0         0       0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auditorium  \
0                     0                 0                   0           0   
1                     0                 0                   0           0   
2                     0                 0                   0           0   
3                     0                 0                   0           0   
4                     0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  Auto Dealership  Auto Garage  \
0                      0                    0                0            0   
1                      0                    0                0            0   
2                      0                    0                0            0   
3                      0                    0                0            0   
4                      0                    0                0            0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Badminton Court  \
0              0                0          0           0                0   
1              0                0          0           0                0   
2              0                0          0           0                0   
3              0                0          0           0                0   
4              0                0          0           0                0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Court  Basketball Stadium  Bath House  Bathing Area  Beach  \
0                 0                   0           0             0      0   
1                 0                   0           0             0      0   
2                 0                   0           0             0      0   
3                 0                   0           0             0      0   
4                 0                   0           0     

In [36]:
#the venue dataframe is now expanded to include the different categories
nyc_london_onehot.shape

(29451, 524)

In [37]:
#group rows by neighborhood and by taking the mean of the frequency of occurrence of each category
nyc_london_grouped = nyc_london_onehot.groupby('Neighborhood').mean().reset_index()
nyc_london_grouped.head()

Neighborhood  ATM  Accessories Store  \
0        Abbey Wood (Bexley,  Greenwich )  0.0                0.0   
1  Acton (Ealing, Hammersmith and Fulham)  0.0                0.0   
2                          Aldgate (City)  0.0                0.0   
3                   Aldwych (Westminster)  0.0                0.0   
4                        Allerton (Bronx)  0.0                0.0   

   Adult Boutique  Afghan Restaurant  African Restaurant  Airport Lounge  \
0             0.0                0.0                 0.0             0.0   
1             0.0                0.0                 0.0             0.0   
2             0.0                0.0                 0.0             0.0   
3             0.0                0.0                 0.0             0.0   
4             0.0                0.0                 0.0             0.0   

   American Restaurant  Animal Shelter  Antique Shop  Aquarium  Arcade  \
0                 0.00             0.0           0.0       0.0     0.0   
1                 0.00             0.0           0.0       0.0     0.0   
2                 0.00             0.0           0.0       0.0     0.0   
3                 0.01             0.0           0.0       0.0     0.0   
4                 0.00             0.0           0.0       0.0     0.0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0               0.0                    0.00         0.00         0.0   
1               0.0                    0.00         0.00         0.0   
2               0.0                    0.01         0.01         0.0   
3               0.0                    0.01         0.01         0.0   
4               0.0                    0.00         0.00         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                  0.0                   0.0              0.00   
1                  0.0                   0.0              0.00   
2                  0.0                   0.0              0.02   
3                  0.0                   0.0              0.00   
4                  0.0                   0.0              0.00   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                 0.0         0.0                    0.0                  0.0   
1                 0.0         0.0                    0.0                  0.0   
2                 0.0         0.0                    0.0                  0.0   
3                 0.0         0.0                    0.0                  0.0   
4                 0.0         0.0                    0.0                  0.0   

   Auto Dealership  Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  \
0              0.0          0.0            0.0            0.000       0.00   
1              0.0          0.0            0.0            0.000       0.00   
2              0.0          0.0            0.0            0.000       0.01   
3              0.0          0.0            0.0            0.000       0.00   
4              0.0          0.0            0.0            0.025       0.00   

   Baby Store  Badminton Court  Bagel Shop    Bakery   Bank    Bar  \
0         0.0              0.0         0.0  0.000000  0.000  0.000   
1         0.0              0.0         0.0  0.038462  0.000  0.000   
2         0.0              0.0         0.0  0.010000  0.000  0.000   
3         0.0              0.0         0.0  0.030000  0.000  0.000   
4         0.0              0.0         0.0  0.000000  0.025  0.025   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0             0.0               0.0               0.0                 0.0   
1             0.0               0.0               0.0                 0.0   
2             0.0               0.0               0.0                 0.0   
3             0.0               0.0               0.0                 0.0   
4             0.0               0.0               0.0                 0.0   

   Bath House  Bathing Area  Beach  Beach 

In [38]:
#verify the number of rows and columns
nyc_london_grouped.shape

(603, 524)

In [39]:
#create the new dataframe and display the top 10 venues for each neighborhood.
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
nyc_london_neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
nyc_london_neighborhoods_venues_sorted['Neighborhood'] = nyc_london_grouped['Neighborhood']

for ind in np.arange(nyc_london_grouped.shape[0]):
    nyc_london_neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(nyc_london_grouped.iloc[ind, :], num_top_venues)

nyc_london_neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0        Abbey Wood (Bexley,  Greenwich )            Campground   
1  Acton (Ealing, Hammersmith and Fulham)  Gym / Fitness Center   
2                          Aldgate (City)           Coffee Shop   
3                   Aldwych (Westminster)                 Hotel   
4                        Allerton (Bronx)           Pizza Place   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0         Grocery Store     Indian Restaurant            Playground   
1                   Pub         Grocery Store                  Park   
2                 Hotel  Gym / Fitness Center            Restaurant   
3           Coffee Shop               Theater                  Café   
4            Donut Shop           Supermarket        Sandwich Place   

  5th Most Common Venue       6th Most Common Venue 7th Most Common Venue  \
0           Zoo Exhibit  Financial or Legal Service          Fishing Spot   
1         Train Station                      Bakery              Pharmacy   
2          Cocktail Bar          Italian Restaurant            Food Truck   
3            Restaurant              Ice Cream Shop                Bakery   
4  Fast Food Restaurant              Discount Store              Pharmacy   

  8th Most Common Venue 9th Most Common Venue     10th Most Common Venue  
0           Fish Market     Fish & Chips Shop                Film Studio  
1     Indian Restaurant           Coffee Shop         Turkish Restaurant  
2                  Café     French Restaurant  Middle Eastern Restaurant  
3            Steakhouse          Dessert Shop         Spanish Restaurant  
4                  Food        Breakfast Spot          Mobile Phone Shop

In [40]:
#verify the number of rows and columns
nyc_london_neighborhoods_venues_sorted.shape

(603, 11)

## Use K-Means to Cluster Neighborhoods Across NYC and London

In [41]:
# set number of clusters
kclusters = 5

nyc_london_grouped_clustering = nyc_london_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(nyc_london_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 4, 4, 0, 1, 1, 0, 1, 0], dtype=int32)

In [42]:
#quick visual on how the clusters are distributed
print(kmeans.labels_)

[1 1 4 4 0 1 1 0 1 0 3 3 3 0 4 4 0 1 1 4 1 1 0 1 4 4 0 0 0 4 2 4 0 1 4 0 4
 0 4 0 1 0 1 0 2 4 1 4 4 1 4 0 4 4 4 0 1 1 1 0 4 0 0 0 4 0 0 1 1 4 1 0 4 0
 0 2 0 1 4 4 1 0 1 1 0 4 1 4 1 4 4 1 0 0 3 4 1 4 4 3 1 4 4 2 4 4 1 1 1 1 1
 4 0 4 1 0 2 4 0 4 4 0 4 1 0 1 4 3 0 0 0 0 0 4 1 1 2 1 0 1 1 4 0 1 1 1 1 0
 4 0 0 4 1 4 0 1 1 1 1 4 1 0 1 0 0 1 0 4 4 0 0 4 0 1 2 1 0 0 1 0 0 0 0 4 2
 4 1 4 1 4 0 4 0 0 0 0 1 1 4 4 4 0 1 3 0 4 1 1 4 0 0 1 0 0 1 1 4 3 4 1 0 0
 0 0 0 4 0 1 4 1 1 4 1 1 1 2 4 1 0 0 1 1 2 1 1 1 0 4 1 0 3 1 1 0 0 1 4 1 0
 0 1 0 1 1 2 1 0 4 1 4 0 4 3 0 1 1 0 0 0 0 1 1 0 4 1 0 0 1 1 4 0 0 1 4 4 1
 1 0 2 4 1 0 4 1 1 1 4 1 4 0 1 0 4 0 1 4 0 1 4 0 1 2 4 0 4 0 0 1 4 0 0 3 1
 4 0 4 1 0 1 4 0 3 4 4 0 1 0 1 2 4 1 4 0 0 0 1 0 2 0 0 4 4 1 3 3 0 1 0 4 1
 0 3 0 1 4 4 2 0 1 1 0 4 1 0 4 1 0 1 4 0 4 1 4 0 0 2 4 0 1 4 1 3 4 4 0 1 1
 0 0 0 1 1 1 1 0 1 0 4 4 0 3 4 0 4 0 0 1 1 0 0 4 3 1 0 2 4 0 0 0 0 0 0 0 0
 4 0 3 4 0 0 0 1 4 0 1 3 0 4 1 1 1 1 4 4 1 4 4 3 1 3 4 4 4 0 0 4 1 0 4 1 0
 4 1 4 1 1 1 4 4 0 0 4 4 

In [43]:
# add clustering labels
nyc_london_neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

merged = nyc_london_neighborhoods

merged = merged.join(nyc_london_neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

merged.head()

City         Neighborhood   Latitude  Longitude  Cluster Labels  \
0  New York City    Wakefield (Bronx)  40.894705 -73.847201               0   
1  New York City   Co-op City (Bronx)  40.874294 -73.829939               0   
2  New York City  Eastchester (Bronx)  40.887556 -73.827806               0   
3  New York City    Fieldston (Bronx)  40.895437 -73.905643               2   
4  New York City    Riverdale (Bronx)  40.890834 -73.912585               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0           Supermarket  Caribbean Restaurant              Pharmacy   
1     Accessories Store   Fried Chicken Joint  Fast Food Restaurant   
2  Fast Food Restaurant  Caribbean Restaurant        Cosmetics Shop   
3                  Park                 Plaza           Bus Station   
4                  Bank            Playground                 Diner   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0  Fast Food Restaurant         Deli / Bodega        Ice Cream Shop   
1           Pizza Place            Restaurant        Mattress Store   
2                 Diner         Bowling Alley         Shopping Mall   
3    Athletics & Sports          Home Service            Playground   
4   Japanese Restaurant              Pharmacy           Pizza Place   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0          Sandwich Place                 Track         Metro Station   
1    Other Great Outdoors    Seafood Restaurant          Liquor Store   
2  Furniture / Home Store         Metro Station          Cocktail Bar   
3             Art Gallery           Coffee Shop           Pizza Place   
4      Mexican Restaurant        Sandwich Place                   Bar   

  10th Most Common Venue  
0                 Bakery  
1         Sandwich Place  
2          Grocery Store  
3                   Café  
4       Tapas Restaurant

In [45]:
# create map
map_clusters = folium.Map(location=[nyc_latitude, nyc_longitude], zoom_start=)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(merged['Latitude'], merged['Longitude'], merged['Neighborhood'], merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Examine Clusters

In [46]:
merged.loc[merged['Cluster Labels'] == 0, merged.columns[[1] + list(range(5, merged.shape[1]))]]

Neighborhood         1st Most Common Venue  \
0                       Wakefield (Bronx)                   Supermarket   
1                      Co-op City (Bronx)             Accessories Store   
2                     Eastchester (Bronx)          Fast Food Restaurant   
4                       Riverdale (Bronx)                          Bank   
5                     Kingsbridge (Bronx)                           Bar   
6                 Marble Hill (Manhattan)                   Pizza Place   
7                        Woodlawn (Bronx)                           Pub   
8                         Norwood (Bronx)                   Pizza Place   
9                  Williamsbridge (Bronx)          Caribbean Restaurant   
10                     Baychester (Bronx)              Department Store   
11                 Pelham Parkway (Bronx)                   Pizza Place   
13                   Bedford Park (Bronx)                   Pizza Place   
14             University Heights (Bronx)                   Pizza Place   
15                 Morris Heights (Bronx)                 Deli / Bodega   
16                        Fordham (Bronx)                    Donut Shop   
17                   East Tremont (Bronx)                   Pizza Place   
18                     West Farms (Bronx)           Fried Chicken Joint   
19                   High  Bridge (Bronx)                   Pizza Place   
20                        Melrose (Bronx)                   Bus Station   
21                     Mott Haven (Bronx)                           Gym   
22                    Port Morris (Bronx)                Baseball Field   
23                       Longwood (Bronx)                Discount Store   
25                     Morrisania (Bronx)                Discount Store   
26                      Soundview (Bronx)          Fast Food Restaurant   
29                   Country Club (Bronx)                 Deli / Bodega   
30                    Parkchester (Bronx)                   Pizza Place   
31             Westchester Square (Bronx)                    Donut Shop   
32                       Van Nest (Bronx)                   Pizza Place   
33                    Morris Park (Bronx)                Sandwich Place   
34                        Belmont (Bronx)            Italian Restaurant   
35                 Spuyten Duyvil (Bronx)                          Bank   
36                North Riverdale (Bronx)                   Pizza Place   
37                     Pelham Bay (Bronx)            Italian Restaurant   
38                  Schuylerville (Bronx)                   Pizza Place   
39                 Edgewater Park (Bronx)                 Deli / Bodega   
40                    Castle Hill (Bronx)                   Bus Station   
41                      Olinville (Bronx)                Sandwich Place   
42                 Pelham Gardens (Bronx)                   Bus Station   
43                      Concourse (Bronx)                   Pizza Place   
44                      Unionport (Bronx)                   Pizza Place   
45                       Edenwald (Bronx)          Caribbean Restaurant   
47                 Bensonhurst (Brooklyn)                    Donut Shop   
48                 Sunset Park (Brooklyn)            Mexican Restaurant   
50                   Gravesend (Brooklyn)                   Pizza Place   
51              Brighton Beach (Brooklyn)                         Beach   
53           Manhattan Terrace (Brooklyn)                   Pizza Place   
54                    Flatbush (Brooklyn)                   Pizza Place   
55               Crown Heights (Brooklyn)                   Pizza Place   
56               East Flatbush (Brooklyn)                Discount Store   
57                  Kensington (Brooklyn)               Thai Restaurant   
60                 Brownsville (Brooklyn)           Fried Chicken Joint   
71               Cypress Hills (Brooklyn)                 Grocery Store   
72               East New York (Brooklyn)             

In [47]:
merged.loc[merged['Cluster Labels'] == 1, merged.columns[[1] + list(range(5, merged.shape[1]))]]

Neighborhood 1st Most Common Venue  \
306                   Abbey Wood (Bexley,  Greenwich )            Campground   
307             Acton (Ealing, Hammersmith and Fulham)  Gym / Fitness Center   
310                                  Anerley (Bromley)         Grocery Store   
311                                  Angel (Islington)         Grocery Store   
312                                Archway (Islington)                   Pub   
314                                Balham (Wandsworth)                   Pub   
315                               Bankside (Southwark)                   Pub   
317                      Barnes (Richmond upon Thames)                  Park   
318                              Barnsbury (Islington)         Grocery Store   
319                             Battersea (Wandsworth)           Coffee Shop   
321                              Bedford Park (Ealing)             Gastropub   
323                              Bellingham (Lewisham)         Train Station   
324                              Belsize Park (Camden)                  Café   
326                      Bethnal Green (Tower Hamlets)                   Pub   
329              Blackheath Royal Standard (Greenwich)    Italian Restaurant   
332                            Bounds Green (Haringey)           Coffee Shop   
333                                Bow (Tower Hamlets)                   Pub   
334                              Bowes Park (Haringey)      Greek Restaurant   
338                                Brockley (Lewisham)                  Café   
339      Bromley (also Bromley-by-Bow) (Tower Hamlets)                   Pub   
341                                Brondesbury (Brent)                   Pub   
343                            Burroughs, The (Barnet)         Grocery Store   
344                             Camberwell (Southwark)                  Café   
345                    Cambridge Heath (Tower Hamlets)           Coffee Shop   
346                               Camden Town (Camden)                   Pub   
348                         Cann Hall (Waltham Forest)         Grocery Store   
350                              Canonbury (Islington)                   Pub   
351                   Castelnau (Richmond upon Thames)                   Pub   
353                                Chalk Farm (Camden)                  Café   
356                   Chelsea (Kensington and Chelsea)                  Café   
359                               Chinbrook (Lewisham)              Platform   
360                         Chingford (Waltham Forest)                   Pub   
361  Chiswick (Hounslow, Ealing, Hammersmith and Fu...           Coffee Shop   
362                                 Church End (Brent)           Coffee Shop   
363                                Church End (Barnet)    Turkish Restaurant   
364                      Clapham (Lambeth, Wandsworth)                   Pub   
366                                 Colindale (Barnet)           Supermarket   
367                             Colliers Wood (Merton)           Coffee Shop   
370                Cricklewood (Barnet, Brent, Camden)              Bus Stop   
371                            Crofton Park (Lewisham)                  Café   
373                              Crouch End (Haringey)                   Pub   
374                           Crystal Palace (Bromley)                  Café   
375                        Cubitt Town (Tower Hamlets)                  Café   
377                                  Dalston (Hackney)                   Pub   
378                       De Beauvoir Town (Islington)                  Café   
379                           Denmark Hill (Southwark)                   Pub   
380                                Deptford (Lewisham)                   Pub   
382                                Dulwich (Southwark)         Grocery Store   
383                                    Ealing (Ealing)                   Pub   
384               Earls Court (Kensington 

In [48]:
merged.loc[merged['Cluster Labels'] == 2, merged.columns[[1] + list(range(5, merged.shape[1]))]]

Neighborhood 1st Most Common Venue  \
3                   Fieldston (Bronx)                  Park   
27               Clason Point (Bronx)                  Park   
76             Mill Island (Brooklyn)            Playground   
91            Bergen Beach (Brooklyn)            Playground   
203         Todt Hill (Staten Island)              Mountain   
287       Egbertville (Staten Island)                  Park   
294                    Malba (Queens)                  Park   
303                Bayswater (Queens)            Playground   
342           Brunswick Park (Barnet)                  Park   
357              Childs Hill (Barnet)                  Park   
372                Crossness (Bexley)                  Park   
415         Hackney Marshes (Hackney)                  Park   
421  Hampstead Garden Suburb (Barnet)                  Park   
436   Horn Park (Greenwich, Lewisham)                   Pub   
454              Lea Bridge (Hackney)                  Park   
479              Mottingham (Bromley)       Motorcycle Shop   
487                 Norbury (Croydon)                  Park   
496                   Osidge (Barnet)         Grocery Store   
513              Raynes Park (Merton)    Athletics & Sports   

    2nd Most Common Venue     3rd Most Common Venue 4th Most Common Venue  \
3                   Plaza               Bus Station    Athletics & Sports   
27                   Pool            Scenic Lookout            Playground   
76        Harbor / Marina        Seafood Restaurant     Other Repair Shop   
91        Harbor / Marina            Baseball Field                  Park   
203                  Park               Zoo Exhibit         Fishing Store   
287                   ATM        Italian Restaurant            Bagel Shop   
294           Bus Station                 Rest Area         Deli / Bodega   
303                  Park              Tennis Court     Indian Restaurant   
342     Electronics Store             Grocery Store                  Café   
357      Sushi Restaurant               Coffee Shop  Gym / Fitness Center   
372       Nature Preserve              Soccer Field                  Lake   
415                  Café                Playground           Film Studio   
421        Breakfast Spot             Grocery Store             Pet Store   
436          Soccer Field                      Park             Pet Store   
454       Nature Preserve                      Café          Skating Rink   
479  Gym / Fitness Center                      Park                   Gym   
487                 River  Mediterranean Restaurant         Grocery Store   
496                  Park        Turkish Restaurant                   Pub   
513                  Park                Playground         Bowling Alley   

       5th Most Common Venue       6th Most Common Venue  \
3               Home Service                  Playground   
27             Boat or Ferry                 Zoo Exhibit   
76                      Park  Tourist Information Center   
91   Comfort Food Restaurant          Athletics & Sports   
203             Fishing Spot                 Fish Market   
287           Clothing Store                         Gym   
294               Playground             Harbor / Marina   
303           Farmers Market                        Farm   
342                 Bus Stop                 Flea Market   
357  Health & Beauty Service                       Hotel   
372              Film Studio               Fishing Store   
415            Fishing Store                Fishing Spot   
421    Outdoors & Recreation                      Bakery   
436            Grocery Store                 Film Studio   
454              Coffee Shop        Gym / Fitness Center   
479        Other Repair Shop        Fast Food Restaurant   
487                   Forest           Convenience Store   
496             Tennis Court                       Plaza   
513     Gym / Fitness Center           Fish & Chips Shop   

    7th Most Common Ve

In [49]:
merged.loc[merged['Cluster Labels'] == 3, merged.columns[[1] + list(range(5, merged.shape[1]))]]

Neighborhood 1st Most Common Venue  \
24                        Hunts Point (Bronx)           Supermarket   
179                         Neponsit (Queens)                 Beach   
205             Port Richmond (Staten Island)              Bus Stop   
206          Mariner's Harbor (Staten Island)              Bus Stop   
217               Tottenville (Staten Island)                  Park   
219               Silver Lake (Staten Island)              Bus Stop   
220                 Sunnyside (Staten Island)              Bus Stop   
224                 Park Hill (Staten Island)              Bus Stop   
227                 Arlington (Staten Island)              Bus Stop   
228                  Arrochar (Staten Island)              Bus Stop   
232             Midland Beach (Staten Island)        Baseball Field   
254                   Concord (Staten Island)              Bus Stop   
256             Randall Manor (Staten Island)              Bus Stop   
285               Willowbrook (Staten Island)              Bus Stop   
286              Sandy Ground (Staten Island)              Bus Stop   
305                 Fox Hills (Staten Island)              Bus Stop   
313                     Arnos Grove (Enfield)         Grocery Store   
352                        Catford (Lewisham)         Grocery Store   
355                      Charlton (Greenwich)              Bus Stop   
407                     Grahame Park (Barnet)                  Park   
427             Highams Park (Waltham Forest)    Turkish Restaurant   
481                           Neasden (Brent)         Shopping Mall   
484                    New Southgate (Barnet)         Grocery Store   
514                   Roehampton (Wandsworth)                   Bar   
525   Snaresbrook (Redbridge, Waltham Forest)    English Restaurant   
562                       Totteridge (Barnet)                Church   
571                       Upton Park (Newham)              Bus Stop   
584                         West Ham (Newham)              Bus Stop   
602  Wormwood Scrubs (Hammersmith and Fulham)              Bus Stop   

    2nd Most Common Venue       3rd Most Common Venue  4th Most Common Venue  \
24         Waste Facility          Chinese Restaurant                   Bank   
179                  Park                    Bus Stop            Pizza Place   
205         Deli / Bodega              Discount Store            Pizza Place   
206   American Restaurant               Grocery Store     Italian Restaurant   
217                 Beach               Deli / Bodega         Cosmetics Shop   
219   American Restaurant                Home Service      Convenience Store   
220           Pizza Place  Construction & Landscaping          Grocery Store   
224         Grocery Store                       Hotel     Chinese Restaurant   
227         Deli / Bodega                Home Service           Intersection   
228        Baseball Field          Italian Restaurant                  Beach   
232                 Beach               Deli / Bodega           Liquor Store   
254           Pizza Place                    Pharmacy          Deli / Bodega   
256                   Bar               Deli / Bodega              Juice Bar   
285    Chinese Restaurant                 Pizza Place                    Spa   
286         Historic Site                  Food Truck      Fish & Chips Shop   
305   American Restaurant               Grocery Store     Athletics & Sports   
313           Pizza Place                    Beer Bar               Bus Stop   
352                  Park           Convenience Store   Gym / Fitness Center   
355           Coffee Shop                 Supermarket                    Pub   
407           Supermarket                    Bus Stop              Gift Shop   
427                   Gym                 Supermarket               Bus Stop   
481         Metro Station              Sandwich Place  Portuguese Restaurant   
484           Pizza Place                    Beer Bar         

In [50]:
merged.loc[merged['Cluster Labels'] == 4, merged.columns[[1] + list(range(5, merged.shape[1]))]]

Neighborhood  \
12                                 City Island (Bronx)   
28                                 Throgs Neck (Bronx)   
46                                Bay Ridge (Brooklyn)   
49                               Greenpoint (Brooklyn)   
52                           Sheepshead Bay (Brooklyn)   
58                          Windsor Terrace (Brooklyn)   
59                         Prospect Heights (Brooklyn)   
61                             Williamsburg (Brooklyn)   
62                                 Bushwick (Brooklyn)   
63                       Bedford Stuyvesant (Brooklyn)   
64                         Brooklyn Heights (Brooklyn)   
65                              Cobble Hill (Brooklyn)   
66                          Carroll Gardens (Brooklyn)   
67                                 Red Hook (Brooklyn)   
68                                  Gowanus (Brooklyn)   
69                              Fort Greene (Brooklyn)   
70                               Park Slope (Brooklyn)   
77                          Manhattan Beach (Brooklyn)   
84                             Clinton Hill (Brooklyn)   
85                                 Sea Gate (Brooklyn)   
86                                 Downtown (Brooklyn)   
87                              Boerum Hill (Brooklyn)   
95                        East Williamsburg (Brooklyn)   
96                               North Side (Brooklyn)   
97                               South Side (Brooklyn)   
98                            Ocean Parkway (Brooklyn)   
100                              Chinatown (Manhattan)   
105                         Central Harlem (Manhattan)   
107                        Upper East Side (Manhattan)   
108                              Yorkville (Manhattan)   
109                             Lenox Hill (Manhattan)   
110                       Roosevelt Island (Manhattan)   
111                        Upper West Side (Manhattan)   
112                         Lincoln Square (Manhattan)   
113                                Clinton (Manhattan)   
114                                Midtown (Manhattan)   
115                            Murray Hill (Manhattan)   
116                                Chelsea (Manhattan)   
117                      Greenwich Village (Manhattan)   
118                           East Village (Manhattan)   
119                        Lower East Side (Manhattan)   
120                                Tribeca (Manhattan)   
121                           Little Italy (Manhattan)   
122                                   Soho (Manhattan)   
123                           West Village (Manhattan)   
124                       Manhattan Valley (Manhattan)   
125                    Morningside Heights (Manhattan)   
126                               Gramercy (Manhattan)   
127                      Battery Park City (Manhattan)   
128                     Financial District (Manhattan)   
129                                   Astoria (Queens)   
135                              Forest Hills (Queens)   
139                          Long Island City (Queens)   
141                             East Elmhurst (Queens)   
150                                Whitestone (Queens)   
151                                   Bayside (Queens)   
173                                  Steinway (Queens)   
176                                  Edgemere (Queens)   
178                            Rockaway Beach (Queens)   
180                               Murray Hill (Queens)   
190                              Belle Harbor (Queens)   
196                      Forest Hills Gardens (Queens)   
197                         St. George (Staten Island)   
201                      West Brighton (Staten Island)   
202                        Grymes Hill (Staten Island)   
204                        South Beach (Staten Island)   
207                         Port Ivory (Staten Island)   
210                             Travis (Staten Island)   
212                            Oakwood (